# Agents AutoGen en Production : Observabilité & Évaluation

Dans ce tutoriel, nous allons apprendre à **surveiller les étapes internes (traces) des [agents Autogen](https://github.com/microsoft/autogen)** et à **évaluer leurs performances** en utilisant [Langfuse](https://langfuse.com).

Ce guide couvre les métriques d'évaluation **en ligne** et **hors ligne** utilisées par les équipes pour mettre rapidement et de manière fiable des agents en production.

**Pourquoi l'évaluation des agents IA est importante :**
- Identifier les problèmes lorsque les tâches échouent ou produisent des résultats sous-optimaux
- Surveiller les coûts et les performances en temps réel
- Améliorer la fiabilité et la sécurité grâce à un retour d'information continu


## Étape 1 : Configurer les variables d'environnement

Obtenez vos clés API Langfuse en vous inscrivant sur [Langfuse Cloud](https://cloud.langfuse.com/) ou en [hébergeant Langfuse vous-même](https://langfuse.com/self-hosting).

_**Remarque :** Les utilisateurs auto-hébergés peuvent utiliser les [modules Terraform](https://langfuse.com/self-hosting/azure) pour déployer Langfuse sur Azure. Alternativement, vous pouvez déployer Langfuse sur Kubernetes en utilisant le [Helm chart](https://langfuse.com/self-hosting/kubernetes-helm)._


In [5]:
import os

# Get keys for your project from the project settings page: https://cloud.langfuse.com
os.environ["LANGFUSE_PUBLIC_KEY"] = "pk-lf-..." 
os.environ["LANGFUSE_SECRET_KEY"] = "sk-lf-..." 
os.environ["LANGFUSE_HOST"] = "https://cloud.langfuse.com" # 🇪🇺 EU region
# os.environ["LANGFUSE_HOST"] = "https://us.cloud.langfuse.com" # 🇺🇸 US region

Avec les variables d'environnement définies, nous pouvons maintenant initialiser le client Langfuse. `get_client()` initialise le client Langfuse en utilisant les identifiants fournis dans les variables d'environnement.


In [6]:
from langfuse import Langfuse
 
# Filter out Autogen OpenTelemetryspans
langfuse = Langfuse(
    blocked_instrumentation_scopes=["autogen SingleThreadedAgentRuntime"]
)
 
# Verify connection
if langfuse.auth_check():
    print("Langfuse client is authenticated and ready!")
else:
    print("Authentication failed. Please check your credentials and host.")

Langfuse client is authenticated and ready!


## Étape 2 : Initialiser l'instrumentation OpenLit

Nous allons maintenant initialiser l'instrumentation [OpenLit](https://github.com/openlit/openlit). OpenLit capture automatiquement les opérations AutoGen et exporte les spans OpenTelemetry (OTel) vers Langfuse.


In [7]:
import openlit
 
# Initialize OpenLIT instrumentation. The disable_batch flag is set to true to process traces immediately.
openlit.init(tracer=langfuse._otel_tracer, disable_batch=True, disabled_instrumentors=["mistral"])

## Étape 3 : Exécutez votre agent

Nous allons maintenant configurer un agent à plusieurs interactions pour tester notre instrumentation.


In [2]:
import os

from autogen_agentchat.agents import AssistantAgent
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_agentchat.base import TaskResult

from autogen_agentchat.conditions import TextMentionTermination
from autogen_agentchat.teams import RoundRobinGroupChat

In [3]:
client = AzureAIChatCompletionClient(
    model="gpt-4o-mini",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.environ["GITHUB_TOKEN"]),
    model_info={
        "json_output": True,
        "function_calling": True,
        "vision": True,
        "family": "unknown",
        "structured_output": False
    },
)

In [8]:
# 🍴 Agent 1 – proposes ONE healthy meal idea each turn
meal_planner_agent = AssistantAgent(
    "meal_planner_agent",
    model_client=client,
    description="A seasoned meal-planning coach who suggests balanced meals.",
    system_message="""
    You are a Meal-Planning Assistant with a decade of experience helping busy people prepare meals.
    Goal: propose the single best meal (breakfast, lunch, or dinner) given the user's context.
    Each response must contain ONLY one complete meal idea (title + very brief component list) — no extras.
    Keep it concise: skip greetings, chit-chat, and filler.
    """,
)

# 🥗 Agent 2 – checks nutritional quality & variety
nutritionist_agent = AssistantAgent(
    "nutritionist_agent",
    model_client=client,
    description="A registered dietitian ensuring meals meet nutritional standards.",
    system_message="""
    You are a Nutritionist focused on whole-food, macro-balanced eating.
    Evaluate the meal_planner_agent’s recommendation.
    If the meal is nutritionally sound, sufficiently varied, and portion-appropriate, respond with 'APPROVE'.
    Otherwise, give high-level guidance on how to improve it (e.g. 'add a plant-based protein') — do NOT provide a full alternative recipe.
    """,
)

In [9]:
# ✅ Chat stops once the nutritionist says APPROVE
termination = TextMentionTermination("APPROVE")

# 🔄 Alternate turns between the two agents until termination
team = RoundRobinGroupChat(
    [meal_planner_agent, nutritionist_agent],
    termination_condition=termination,
)

# Example kickoff
user_input = "I'm looking for a quick, delicious dinner I can prep after work. I have 30 minutes and minimal clean-up is ideal."

In [ ]:
with langfuse.start_as_current_span(name="create_meal_plan") as span:
    async for message in team.run_stream(task=user_input):
        if isinstance(message, TaskResult):
            print("Stop Reason:", message.stop_reason)
        else:
            print(message)

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

# Flush the trace to Langfuse for short-lived environments such as Jupyter Notebooks
langfuse.flush()

### Structure de la trace

Langfuse enregistre une **trace** qui contient des **spans**, représentant chaque étape de la logique de votre agent. Ici, la trace inclut l'exécution globale de l'agent ainsi que des sous-spans pour :
- L'agent planificateur de repas
- Les agents nutritionnistes

Vous pouvez les examiner pour voir précisément où le temps est passé, combien de tokens sont utilisés, et ainsi de suite :

![Arbre de trace dans Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/trace-tree.png)

_[Lien vers la trace](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


## Évaluation en ligne

L'évaluation en ligne consiste à évaluer l'agent dans un environnement réel et en direct, c'est-à-dire pendant son utilisation réelle en production. Cela implique de surveiller en continu les performances de l'agent lors des interactions avec les utilisateurs et d'analyser les résultats.

### Métriques courantes à suivre en production

1. **Coûts** — L'instrumentation capture l'utilisation des tokens, que vous pouvez transformer en coûts approximatifs en attribuant un prix par token.
2. **Latence** — Observez le temps nécessaire pour compléter chaque étape ou l'ensemble du processus.
3. **Retour des utilisateurs** — Les utilisateurs peuvent fournir des retours directs (pouce levé/baissé) pour aider à affiner ou corriger l'agent.
4. **LLM comme juge** — Utilisez un LLM distinct pour évaluer les résultats de votre agent en quasi temps réel (par exemple, vérifier la toxicité ou la justesse).

Ci-dessous, nous montrons des exemples de ces métriques.


#### 1. Coûts

Ci-dessous, une capture d'écran montrant l'utilisation des appels `gpt-4o-mini`. Cela permet d'identifier les étapes coûteuses et d'optimiser votre agent.

![Coûts](https://langfuse.com/images/cookbook/example-autogen-evaluation/gpt-4o-costs.png) 

_[Lien vers la trace](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


#### 2. Latence

Nous pouvons également observer combien de temps chaque étape a pris pour être complétée. Dans l'exemple ci-dessous, l'exécution complète a duré environ 3 secondes, que vous pouvez décomposer étape par étape. Cela vous aide à identifier les goulots d'étranglement et à optimiser votre agent.

![Latence](https://langfuse.com/images/cookbook/example-autogen-evaluation/agent-latency.png) 

_[Lien vers la trace](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64?display=timeline)_


#### 3. Retour des utilisateurs

Si votre agent est intégré dans une interface utilisateur, vous pouvez enregistrer directement les retours des utilisateurs (comme un pouce levé/baissé dans une interface de chat).


In [10]:
from langfuse import get_client
 
langfuse = get_client()
 
# Option 1: Use the yielded span object from the context manager
with langfuse.start_as_current_span(
    name="autogen-request-user-feedback-1") as span:
    
    async for message in team.run_stream(task="Create a meal with potatoes"):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using the span object
    span.score_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC",
        comment="This was delicious, thank you"
    )
 
# Option 2: Use langfuse.score_current_trace() if still in context
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:
    # ... Autogen execution ...

    async for message in team.run_stream(task="I am allergic to gluten."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using current context
    langfuse.score_current_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC"
    )

id='da068880-22ae-4f01-9f01-2bb231939089' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 43, 732669, tzinfo=datetime.timezone.utc) content='Create a meal with potatoes' type='TextMessage'
id='ad937ce4-3534-493f-824b-ca9c226b5287' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=95, completion_tokens=30) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 186423, tzinfo=datetime.timezone.utc) content='Potato and Spinach Frittata  \n- Eggs  \n- Potatoes  \n- Fresh spinach  \n- Onion  \n- Cheese (optional)  ' type='TextMessage'
id='50fd33c1-057f-49fe-afad-ee86d164296d' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=132, completion_tokens=4) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 581059, tzinfo=datetime.timezone.utc) content='APPROVE' type='TextMessage'
Stop Reason: Text 'APPROVE' mentioned
id='e371de6c-e5fc-42c1-8eda-e5b8cd5accab' source='user' models_usage=None met

In [ ]:
# Option 3: Use create_score() with trace ID (when outside context)
langfuse.create_score(
    trace_id="predefined_trace_id",
    name="user-feedback",
    value=1,
    data_type="NUMERIC",
    comment="This was correct, thank you"
)

Les retours des utilisateurs sont ensuite enregistrés dans Langfuse :

![Les retours des utilisateurs sont enregistrés dans Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/user-feedback.png)


#### 4. Évaluation automatisée avec LLM-as-a-Judge

LLM-as-a-Judge est une autre méthode pour évaluer automatiquement les résultats de votre agent. Vous pouvez configurer un appel LLM distinct pour évaluer la justesse, la toxicité, le style ou tout autre critère qui vous intéresse.

**Flux de travail** :
1. Vous définissez un **Modèle d'Évaluation**, par exemple : "Vérifiez si le texte est toxique."
2. Vous configurez un modèle utilisé comme modèle-juge ; dans ce cas, `gpt-4o-mini` interrogé via Azure.
3. Chaque fois que votre agent génère un résultat, vous transmettez ce résultat à votre LLM "juge" avec le modèle d'évaluation.
4. Le LLM juge répond avec une note ou une étiquette que vous enregistrez dans votre outil d'observabilité.

Exemple tiré de Langfuse :

![Évaluateur LLM-as-a-Judge](https://langfuse.com/images/cookbook/example-autogen-evaluation/evaluator.png)


In [12]:
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:

    async for message in team.run_stream(task="I am a picky eater and not sure if you find something for me."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message) 

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

langfuse.flush()

id='eefc628d-502f-451a-8f70-be486f62f8c5' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 29, 171393, tzinfo=datetime.timezone.utc) content='I am a picky eater and not sure if you find something for me.' type='TextMessage'
id='13b3e14b-bcf7-42a5-80d6-54b0c7be765e' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=352, completion_tokens=27) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 30, 433516, tzinfo=datetime.timezone.utc) content='Chicken Alfredo Pasta  \n- Gluten-free pasta  \n- Grilled chicken breast  \n- Heavy cream  \n- Parmesan cheese  \n- Garlic  ' type='TextMessage'
id='550f2dee-0e08-4bbd-b67f-991b467328f1' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=386, completion_tokens=17) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 31, 505173, tzinfo=datetime.timezone.utc) content='Consider incorporating some vegetables, like spinach or broccoli, to increase the nutrien

Vous pouvez voir que la réponse de cet exemple est jugée comme "non toxique".

![Score d'évaluation LLM-en-tant-que-Juge](https://langfuse.com/images/cookbook/example-autogen-evaluation/llm-as-a-judge-score.png)


#### 5. Aperçu des métriques d'observabilité

Toutes ces métriques peuvent être visualisées ensemble dans des tableaux de bord. Cela vous permet de voir rapidement les performances de votre agent sur de nombreuses sessions et de suivre les métriques de qualité au fil du temps.

![Aperçu des métriques d'observabilité](https://langfuse.com/images/cookbook/example-autogen-evaluation/dashboard.png)


## Évaluation hors ligne

L'évaluation en ligne est essentielle pour obtenir des retours en temps réel, mais vous avez également besoin d'une **évaluation hors ligne**—des vérifications systématiques avant ou pendant le développement. Cela permet de garantir la qualité et la fiabilité avant de déployer des modifications en production.


### Évaluation du jeu de données

Lors d'une évaluation hors ligne, vous procédez généralement ainsi :
1. Vous disposez d'un jeu de données de référence (avec des paires de prompts et de résultats attendus)
2. Vous exécutez votre agent sur ce jeu de données
3. Vous comparez les résultats obtenus aux résultats attendus ou utilisez un mécanisme de notation supplémentaire

Ci-dessous, nous illustrons cette approche avec le [q&a-dataset](https://huggingface.co/datasets/junzhang1207/search-dataset), qui contient des questions et des réponses attendues.


In [16]:
import pandas as pd
from datasets import load_dataset
 
# Fetch search-dataset from Hugging Face
dataset = load_dataset("junzhang1207/search-dataset", split = "train")
df = pd.DataFrame(dataset)
print("First few rows of search-dataset:")
print(df.head())

/Users/jannik/Documents/GitHub/ai-agents-for-beginners/.venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


First few rows of search-dataset:
                                     id  \
0  20caf138-0c81-4ef9-be60-fe919e0d68d4   
1  1f37d9fd-1bcc-4f79-b004-bc0e1e944033   
2  76173a7f-d645-4e3e-8e0d-cca139e00ebe   
3  5f5ef4ca-91fe-4610-a8a9-e15b12e3c803   
4  64dbed0d-d91b-4acd-9a9c-0a7aa83115ec   

                                            question  \
0                 steve jobs statue location budapst   
1  Why is the Battle of Stalingrad considered a t...   
2  In what year did 'The Birth of a Nation' surpa...   
3  How many Russian soldiers surrendered to AFU i...   
4   What event led to the creation of Google Images?   

                                     expected_answer       category       area  
0  The Steve Jobs statue is located in Budapest, ...           Arts  Knowledge  
1  The Battle of Stalingrad is considered a turni...   General News       News  
2  This question is based on a false premise. 'Th...  Entertainment       News  
3  About 300 Russian soldiers surrendered to t

Ensuite, nous créons une entité de jeu de données dans Langfuse pour suivre les exécutions. Ensuite, nous ajoutons chaque élément du jeu de données au système.


In [17]:
from langfuse import Langfuse
langfuse = Langfuse()
 
langfuse_dataset_name = "qa-dataset_autogen-agent"
 
# Create a dataset in Langfuse
langfuse.create_dataset(
    name=langfuse_dataset_name,
    description="q&a dataset uploaded from Hugging Face",
    metadata={
        "date": "2025-03-21",
        "type": "benchmark"
    }
)

Dataset(id='cmcm7524d00kjad07s2cjwqcf', name='qa-dataset_autogen-agent', description='q&a dataset uploaded from Hugging Face', metadata={'date': '2025-03-21', 'type': 'benchmark'}, project_id='cloramnkj0002jz088vzn1ja4', created_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc), updated_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc))

In [18]:
df_25 = df.sample(25) # For this example, we upload only 25 dataset questions

for idx, row in df_25.iterrows():
    langfuse.create_dataset_item(
        dataset_name=langfuse_dataset_name,
        input={"text": row["question"]},
        expected_output={"text": row["expected_answer"]}
    )

![Éléments du jeu de données dans Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/example-dataset.png)


#### Exécution de l'agent sur le jeu de données

Tout d'abord, nous assemblons un agent Autogen simple qui répond aux questions en utilisant les modèles Azure OpenAI.


In [8]:
import os
from dotenv import load_dotenv

from autogen_agentchat.agents import AssistantAgent
from autogen_core.models import UserMessage
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_core import CancellationToken
from autogen_agentchat.messages import TextMessage

In [ ]:
load_dotenv()
client = AzureAIChatCompletionClient(
    model="gpt-4o",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.getenv("GITHUB_TOKEN")),
    max_tokens=5000,
    model_info={
        "json_output": True,
        "function_calling": False,
        "vision": False,
        "family": "unknown",
        "structured_output": True,
    },
)

result = await client.create([UserMessage(content="What is the capital of France?", source="user")])
print(result)

In [18]:
agent = AssistantAgent(
    name="assistant",
    model_client=client,
    tools=[],
    system_message="You are participant in a quizz show and you are given a question. You need to create a short answer to the question.",
)

Ensuite, nous définissons une fonction auxiliaire `my_agent()`.


In [19]:
async def my_agent(user_query: str):

    with langfuse.start_as_current_span(name="autogen-trace") as span:

        # Execute the agent response
        response = await agent.on_messages(
            [TextMessage(content=user_query, source="user")],
            cancellation_token=CancellationToken(),
        )

        span.update_trace(
            input=user_query,
            output=response.chat_message.content,
        )

    return str(response.chat_message.content)

# Test the function
await my_agent("What is the capital of France?")

'The capital of France is Paris.'

Enfin, nous parcourons chaque élément du jeu de données, exécutons l'agent et relions la trace à l'élément du jeu de données. Nous pouvons également ajouter un score d'évaluation rapide si souhaité.


In [20]:
dataset_name = "qa-dataset_autogen-agent"
current_run_name = "dev_tasks_run-autogen_gpt-4.1" # Identifies this specific evaluation run
current_run_metadata={"model_provider": "Azure", "model": "gpt-4.1"}
current_run_description="Evaluation run for Autogen model on July 3rd"

dataset = langfuse.get_dataset('qa-dataset_autogen-agent')

for item in dataset.items:
    print(f"Running evaluation for item: {item.id} (Input: {item.input})")
 
    # Use the item.run() context manager
    with item.run(
        run_name=current_run_name,
        run_metadata=current_run_metadata,
        run_description=current_run_description
    ) as root_span: 
        # All subsequent langfuse operations within this block are part of this trace.
        generated_answer = await my_agent(user_query = item.input["text"])
    
    print("Generated Answer: ", generated_answer)
 
print(f"\nFinished processing dataset '{dataset_name}' for run '{current_run_name}'.")

langfuse.flush()

Running evaluation for item: 09810cc4-9992-4712-a3b2-7224da31776a (Input: {'text': 'In Hindu mythology, which deity is the Ganges river dolphin associated with?'})
Generated Answer:  In Hindu mythology, the Ganges river dolphin is associated with the deity Ganga.
Running evaluation for item: bb113f94-7723-47c6-8c34-59d883044514 (Input: {'text': 'What significant discovery did the LHCb collaboration report in 2015?'})
Generated Answer:  In 2015, the LHCb collaboration reported the discovery of pentaquark particles.
Running evaluation for item: 4d8ae54e-ceab-46d0-ad2c-6e8e223589a9 (Input: {'text': 'What is the MÄ\x81ori name for the red-crowned parakeet?'})
Generated Answer:  The Māori name for the red-crowned parakeet is kākāriki.
Running evaluation for item: 21e5a0d5-f619-4a73-868e-9955053b3e72 (Input: {'text': 'Who starred in the 1978 television film adaptation of Les MisÃ©rables?'})
Generated Answer:  Richard Jordan starred as Jean Valjean in the 1978 television film adaptation of Le

Vous pouvez répéter ce processus avec différentes configurations d'agent telles que :
- Modèles (gpt-4o-mini, gpt-4.1, etc.)
- Prompts
- Outils (recherche vs. pas de recherche)
- Complexité de l'agent (multi-agent vs agent unique)

Ensuite, comparez-les côte à côte dans Langfuse. Dans cet exemple, j'ai exécuté l'agent 3 fois sur les 25 questions du jeu de données. Pour chaque exécution, j'ai utilisé un modèle Azure OpenAI différent. Vous pouvez constater que le nombre de questions correctement répondues augmente avec l'utilisation d'un modèle plus grand (comme prévu). Le score `correct_answer` est créé par un [Évaluateur LLM-as-a-Judge](https://langfuse.com/docs/scores/model-based-evals) qui est configuré pour juger de la justesse de la réponse en fonction de la réponse exemple donnée dans le jeu de données.

![Aperçu des exécutions du jeu de données](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset_runs.png)
![Comparaison des exécutions du jeu de données](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset-run-comparison.png)



---

**Avertissement** :  
Ce document a été traduit à l'aide du service de traduction automatique [Co-op Translator](https://github.com/Azure/co-op-translator). Bien que nous nous efforcions d'assurer l'exactitude, veuillez noter que les traductions automatisées peuvent contenir des erreurs ou des inexactitudes. Le document original dans sa langue d'origine doit être considéré comme la source faisant autorité. Pour des informations critiques, il est recommandé de recourir à une traduction professionnelle réalisée par un humain. Nous déclinons toute responsabilité en cas de malentendus ou d'interprétations erronées résultant de l'utilisation de cette traduction.
